## Домашнее задание

Основаная задача - **построить хорошую тематическую модель с интерпретируемыми топиками с помощью LDA в gensim и NMF в sklearn**.


1) сделайте нормализацию (если pymorphy2 работает долго используйте mystem или попробуйте установить быструю версию - `pip install pymorphy2[fast]`, можно использовать какой-то другой токенизатор); 

2) добавьте нграммы (в тетрадке есть закомменченая ячейка с Phrases,  можно также попробовать другие способы построить нграммы); 

3) сделайте хороший словарь (отфильтруйте слишком частотные и редкие слова, попробуйте удалить стоп-слова); 

4) постройте несколько LDA моделей (переберите количество тем, можете поменять eta, alpha, passes), если получаются плохие темы, поработайте дополнительно над предобработкой и словарем; 

5) для самой хорошей модели в отдельной ячейке напечатайте 3 хороших (на ваш вкус) темы;

6) между словарем и обучением модели добавьте tfidf (`gensim.models.TfidfModel(corpus, id2word=dictionary); corpus = tfidf[corpus]`);

7) повторите пункт 4 на преобразованном корпусе;

8) в отдельной ячейке опишите как изменилась модель (приведите несколько тем, которые стали лучше или хуже, или которых раньше вообще не было; можно привести значения перплексии и когерентности для обеих моделей)

9) проделайте такие же действия для NMF (образец в конце тетрадки), для построения словаря воспользуйтесь возможностями Count или Tfidf Vectorizer (попробуйте другие значение max_features, min_df, max_df, сделайте нграмы через ngram_range, если хватает памяти), попробуйте такие же количества тем

10) в отдельной ячейки напечатайте таблицу с темами лучшей NMF модели, сравните их с теми, что получились в LDA.

Сохраните тетрадку с экспериментами и положите её на гитхаб, ссылку на неё укажите в форме.

**Оцениваться будут главным образом пункты 5, 8 и 10. (2, 3, 2 баллов соответственно). Чтобы заработать остальные 3 балла, нужно хотя бы немного изменить мой код на промежуточных этапах (добавить что-то, указать другие параметры и т.д). **

In [1]:
import gensim
import json
import re
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
from pymorphy2 import MorphAnalyzer
import pyLDAvis.gensim
import string
from collections import Counter
import warnings
warnings.filterwarnings("ignore")

morph = MorphAnalyzer()

## Данные

In [107]:
stops = set(stopwords.words('russian')) | {'gt',}
def remove_tags(text):
    return re.sub(r'<[^>]+>', '', text)

def normalize(words):
    norm_words = [morph.parse(word)[0].normal_form for word in words if len(set(word)) > 1]
    return norm_words

def opt_normalize(texts, top=None):
    uniq = Counter()
    for text in texts:
        uniq.update(text)
    
    norm_uniq = {word:morph.parse(word)[0].normal_form for word, _ in uniq.most_common(top)}
    
    norm_texts = []
    for text in texts:
        
        norm_words = [norm_uniq.get(word) for word in text]
        norm_words = [word for word in norm_words if word and word not in stops]
        norm_texts.append(norm_words)
        
    return norm_texts

def tokenize(text):
    words = [word.strip(string.punctuation) for word in text.split()]
    words = [word for word in words if word]
    
    return words

Возьмем 4 тыс статьи с Хабра. Это мало для хорошей тематической модели, но иначе у нас просто ничего не обучится за семинар.

In [ ]:
# f = open('habr_texts.vw', 'w')

# for i, text in enumerate(habr_texts):
#     c = Counter(text)
#     doc = 'doc_'+ str(i) + ' '
#     vw_text = ' '.join([x+':'+str(c[x]) for x in c])
    
#     f.write(doc + vw_text  + '\n')
# f.close()



В текстах есть тэги. Потрем их. Ещё токенизируем самым простым способом и нормализуем Pymorphy.

In [108]:
%%time
texts = open('habr_texts.txt').read().splitlines()
texts = [tokenize(remove_tags(text.lower())) for text in texts]

CPU times: user 1.98 s, sys: 263 ms, total: 2.24 s
Wall time: 2.24 s


In [109]:
%%time
texts = open('habr_texts.txt').read().splitlines()
texts = [normalize(tokenize(text.lower())) for text in texts]

CPU times: user 1min 30s, sys: 1.13 s, total: 1min 31s
Wall time: 1min 31s


In [110]:
%%time
texts = open('habr_texts.txt').read().splitlines()
texts = opt_normalize([tokenize(remove_tags(text.lower())) for text in texts], 30000)

CPU times: user 5.47 s, sys: 309 ms, total: 5.78 s
Wall time: 5.76 s


In [7]:
#для нграммов
ph = gensim.models.Phrases(texts, scoring='npmi', threshold=0.4) # threshold можно подбирать
p = gensim.models.phrases.Phraser(ph)
ngrammed_texts = p[texts]

In [54]:
texts = ngrammed_texts

### Тематическое моделирование в gensim

Для моделей нужно сделать словарь.

In [46]:
dictinary = gensim.corpora.Dictionary(ngrammed_texts)

In [47]:
dictinary.filter_extremes(no_above=0.3)
dictinary.compactify()

In [48]:
print(dictinary)

Dictionary(16828 unique tokens: ['falcon_heavy', 'компьютерный_зрение', 'подписаться', 'транспортный_средство', 'считаться']...)


Преобразуем наши тексты в мешки слов. 

In [55]:
corpus = [dictinary.doc2bow(text) for text in texts]
# если текстов много, то тут может быть генератор

In [12]:
?gensim.models.LdaMulticore

In [56]:
%%time
lda = gensim.models.LdaMulticore(corpus, 100, id2word=dictinary, passes=5, eta='auto', iterations=10, workers=8) # если поддерживается многопоточность
#lsi = gensim.models.LdaModel(200, id2word=dictinary, passes=5, workers=8)

CPU times: user 35.2 s, sys: 17.4 s, total: 52.5 s
Wall time: 54.3 s


Посмотрим на топики.

Ещё есть штука для визуализации.

In [57]:
pyLDAvis.enable_notebook()

In [58]:
pyLDAvis.gensim.prepare(lda, corpus, dictinary)

PreparedData(topic_coordinates=           Freq  cluster  topics         x         y
topic                                               
78     8.874249        1       1 -0.146615 -0.009439
11     5.646791        1       2  0.171004 -0.013121
17     4.909006        1       3  0.113603  0.089015
95     4.653948        1       4  0.212135 -0.059435
86     4.639486        1       5 -0.082592 -0.012592
91     4.007500        1       6 -0.068853 -0.039466
82     3.642625        1       7 -0.019971 -0.016818
50     3.330781        1       8 -0.081633  0.026653
47     2.335723        1       9 -0.058627  0.041275
76     2.298773        1      10 -0.062031  0.000856
72     2.181145        1      11 -0.071045  0.026960
29     2.158661        1      12 -0.089049 -0.055116
28     2.108724        1      13 -0.105052 -0.061068
52     2.047714        1      14 -0.026535  0.058944
81     1.924899        1      15 -0.077808 -0.031007
34     1.687877        1      16  0.002234  0.103705
66     1.641702        1      17 -0.004049  0.008848
41     1.634858        1      18  0.060013 -0.092037
7      1.628526        1      19 -0.028430  0.037675
19     1.604129        1      20 -0.025264  0.083146
63     1.588169        1      21 -0.028563  0.009268
25     1.464319        1      22 -0.086668 -0.046551
67     1.257991        1      23 -0.044384 -0.006899
21     1.243589        1      24 -0.019036  0.048269
94     1.208524        1      25  0.112757 -0.049958
61     1.117179        1      26 -0.057843 -0.014519
26     1.089646        1      27 -0.067713  0.015081
49     0.960850        1      28  0.022680  0.078440
57     0.954126        1      29  0.020961  0.038180
77     0.888275        1      30 -0.010864  0.077295
...         ...      ...     ...       ...       ...
74     0.207398        1      71 -0.003855  0.002123
24     0.192777        1      72  0.044183  0.024849
62     0.192487        1      73 -0.007925 -0.017115
89     0.180342        1      74  0.019816  0.006369
10     0.178051        1      75 -0.011888  0.011233
4      0.172950        1      76  0.009336  0.007350
37     0.167896        1      77  0.017842 -0.002836
30     0.162458        1      78 -0.004279 -0.012123
13     0.153614        1      79  0.027261 -0.024074
80     0.149850        1      80  0.020408  0.009937
16     0.146967        1      81 -0.008982 -0.011102
42     0.146602        1      82  0.016101 -0.021638
71     0.139787        1      83 -0.001030 -0.000736
43     0.130643        1      84 -0.014957  0.015827
15     0.122813        1      85  0.028594 -0.019631
60     0.099643        1      86  0.017359 -0.025710
79     0.093676        1      87 -0.016289  0.006848
96     0.092681        1      88  0.009824  0.001184
20     0.088419        1      89  0.005306  0.008401
45     0.083861        1      90  0.008898  0.001799
0      0.082300        1      91  0.002426 -0.011653
3      0.074848        1      92  0.006828  0.003286
56     0.072002        1      93  0.007103 -0.011110
38     0.063417        1      94  0.023970 -0.004234
98     0.053458        1      95  0.005542 -0.016141
33     0.052561        1      96 -0.002810 -0.013802
44     0.051652        1      97  0.015258 -0.011111
40     0.043302        1      98  0.020531 -0.008154
36     0.036486        1      99 -0.004289 -0.011061
88     0.008402        1     100  0.006759 -0.003241

[100 rows x 5 columns], topic_info=       Category         Freq        Term        Total  loglift  logprob
term                                                                   
5604    Default  5485.000000        игра  5485.000000  30.0000  30.0000
6075    Default  4444.000000           0  4444.000000  29.0000  29.0000
15537   Default  5396.000000        файл  5396.000000  28.0000  28.0000
7142    Default  4171.000000    значение  4171.000000  27.0000  27.0000
15456   Default  3742.000000      объект  3742.000000  26.0000  26.0000
2488    Default  3411.000000      return  3411.000000  25.0000  25.0000
5773    Default  4

Можно посмотреть метрики.

In [59]:
import numpy as np

In [60]:
?lda.log_perplexity

In [61]:
lda.log_perplexity(corpus[:2000], total_docs=100)

-30.60357282691637

In [62]:
coherence_model_lda = gensim.models.CoherenceModel(model=lda, 
                                                   texts=texts, 
                                                   dictionary=dictinary, coherence='c_v')

In [63]:
topics = []
for topic_id, topic in lda.show_topics(num_topics=100, formatted=False):
    topic = [word for word, _ in topic]
    topics.append(topic)

In [64]:
import pandas as pd

In [65]:
pd.DataFrame(topics).head(10)

0           1              2              3           4  \
0    qualcomm       apple  производитель  переключатель         чип   
1       react   компонент            jsx     компонента       метод   
2      сервер  устройство         сигнал     управление      доступ   
3      список      сервис           файл          метод     корабль   
4         php  infiniband           сеть           свет  устройство   
5  инструмент      объект             ms       значение      ошибка   
6     элемент   компонент       страница           файл      список   
7   процессор      память           сайт       скорость        игра   
8       точка       ребро          класс            луч    алгоритм   
9      камера  устройство           сайт         сервис  технология   

               5           6                   7            8  \
0     устройство  технология             таблица            0   
1      состояние  библиотека              виджет      браузер   
2      настройка        сеть              камера       облако   
3          d-bus   сообщение              запрос     значение   
4      сообщение     быстрый            протокол     значение   
5      sonarqube        язык          pvs-studio      элемент   
6         ссылка   состояние             браузер  уведомление   
7          объём  видеокарта  производительность        набор   
8       значение       метод               scala         блок   
9  производитель   заголовок                цвет        цвета   

                    9  
0                 ггц  
1       render_return  
2                ключ  
3              сервер  
4  производительность  
5              анализ  
6                 dom  
7              сервер  
8            добавить  
9              модель

In [66]:
coherence_model_lda = gensim.models.CoherenceModel(topics=topics, 
                                                   texts=texts, 
                                                   dictionary=dictinary, coherence='c_v')

In [67]:
coherence_model_lda.get_coherence()

0.44010534263880324

In [72]:
eta = ['auto', 0.01, 0.1, 0.5, 1]
ntopics = [10, 50, 100, 200, 500]

In [73]:
from itertools import product

In [74]:
for i in product(eta, ntopics):
    print ('e={}, n={}'.format(*i), end='\t')
    lda = gensim.models.LdaMulticore(corpus, i[1], id2word=dictinary, passes=5, eta=i[0], iterations=10, workers=8)
    
    print (lda.log_perplexity(corpus[:2000], total_docs=100), end='\t')
    
    topics = []
    for topic_id, topic in lda.show_topics(num_topics=100, formatted=False):
        topic = [word for word, _ in topic]
        topics.append(topic)
    
    coherence_model_lda = gensim.models.CoherenceModel(topics=topics, 
                                                   texts=texts, 
                                                   dictionary=dictinary, coherence='c_v')
    print (coherence_model_lda.get_coherence())

e=auto, n=10	-12.202549394835051	0.4003135917636268
e=auto, n=50	-21.948581613832868	0.4724256740454048
e=auto, n=100	-30.51693016052195	0.4603710804152907
e=auto, n=200	-45.24818967544526	0.4516010699157512
e=auto, n=500	-82.11359649744384	0.4060038283880914
e=0.01, n=10	-21.108770968216287	0.41867684652694426
e=0.01, n=50	-46.2274911605714	0.46537130496599177
e=0.01, n=100	-59.745446516634146	0.4612736049954438
e=0.01, n=200	-73.78387166869591	0.42386239651595076
e=0.01, n=500	-94.34472658578889	0.380623594292187
e=0.1, n=10	-14.695269301661837	0.40810602761488324
e=0.1, n=50	-23.800437590487277	0.4521520433681841
e=0.1, n=100	-28.44911703344875	0.46515371234013647
e=0.1, n=200	-31.469300043434725	0.4080372527503499
e=0.1, n=500	-36.281602375715615	0.39423487720265543
e=0.5, n=10	-12.901462860562237	0.4181932884790676
e=0.5, n=50	-19.253058207282493	0.41029883167729375
e=0.5, n=100	-20.855778679377426	0.42345093253341676
e=0.5, n=200	-19.650668711450564	0.4037703017058928
e=0.5, n=50

In [75]:
for i in [5, 10, 25, 50, 100]:
    print ('passes={}'.format(i), end='\t')
    lda = gensim.models.LdaMulticore(corpus, 50, id2word=dictinary, passes=5, eta=0.01, iterations=10, workers=8)
    
    print (lda.log_perplexity(corpus[:2000], total_docs=100), end='\t')
    
    topics = []
    for topic_id, topic in lda.show_topics(num_topics=100, formatted=False):
        topic = [word for word, _ in topic]
        topics.append(topic)
    
    coherence_model_lda = gensim.models.CoherenceModel(topics=topics, 
                                                   texts=texts, 
                                                   dictionary=dictinary, coherence='c_v')
    print (coherence_model_lda.get_coherence())

passes=5	-45.9866513767486	0.4518958419214364
passes=10	-45.819185861232896	0.45729912907708964
passes=25	-46.24849879985393	0.46894137432082145
passes=50	-46.07198293903265	0.45930129228423494
passes=100	-45.976000927547716	0.45261446956576246


In [77]:
lda = gensim.models.LdaMulticore(corpus, 50, id2word=dictinary, passes=25, eta=0.01, iterations=10, workers=8)    

topics = []
for topic_id, topic in lda.show_topics(num_topics=50, formatted=False):
        topic = [word for word, _ in topic]
        topics.append(topic)

In [87]:
pd.DataFrame([topics[8]]+[topics[9]]+[topics[12]])

0         1       2        3          4        5          6  \
0  контейнер  участник  docker    набор  хранилище   пароль    windows   
1        ibm   пациент    врач  лечение     анализ  болезнь     watson   
2  microsoft      окно  список  windows    выбрать     меню  настройка   

           7            8            9  
0     секрет      выбрать  собственный  
1   препарат  заболевание  когнитивный  
2  интерфейс    доступный   обновление

In [89]:
tfidf = gensim.models.TfidfModel(corpus, id2word=dictinary)
corpus = tfidf[corpus]

In [90]:
for i in product(eta, ntopics):
    print ('e={}, n={}'.format(*i), end='\t')
    lda = gensim.models.LdaMulticore(corpus, i[1], id2word=dictinary, passes=5, eta=i[0], iterations=10, workers=8)
    
    print (lda.log_perplexity(corpus[:2000], total_docs=100), end='\t')
    
    topics = []
    for topic_id, topic in lda.show_topics(num_topics=100, formatted=False):
        topic = [word for word, _ in topic]
        topics.append(topic)
    
    coherence_model_lda = gensim.models.CoherenceModel(topics=topics, 
                                                   texts=texts, 
                                                   dictionary=dictinary, coherence='c_v')
    print (coherence_model_lda.get_coherence())

e=auto, n=10	-24.193545917276907	0.34768143185540573
e=auto, n=50	-89.38251875953145	0.443440706856199
e=auto, n=100	-141.50099655547916	0.4636302928726802
e=auto, n=200	-237.54851235864282	0.42315745398661436
e=auto, n=500	-480.92088547176536	0.377286291473304
e=0.01, n=10	-170.4060243708794	0.4564101834560562
e=0.01, n=50	-216.55456832251681	0.4476426864954896
e=0.01, n=100	-225.29414932949553	0.44767801591372447
e=0.01, n=200	-243.68213634439115	0.4373240176956755
e=0.01, n=500	-265.68805033960786	0.4012492096106751
e=0.1, n=10	-52.617817841343324	0.39998435607850247
e=0.1, n=50	-55.9729069073376	0.4957527917469472
e=0.1, n=100	-50.72690839921991	0.4715168220648862
e=0.1, n=200	-51.87559387638396	0.4557163661803779
e=0.1, n=500	-53.55771896807704	0.3797497279559907
e=0.5, n=10	-23.32894935675583	0.32579126621513865
e=0.5, n=50	-21.87875567695318	0.36328926008283063
e=0.5, n=100	-21.84200797224974	0.36742415364584874
e=0.5, n=200	-19.797367095680205	0.34649040412272475
e=0.5, n=500	-

In [91]:
lda = gensim.models.LdaMulticore(corpus, 50, id2word=dictinary, passes=25, eta=0.1, iterations=10, workers=8)    

topics = []
for topic_id, topic in lda.show_topics(num_topics=50, formatted=False):
        topic = [word for word, _ in topic]
        topics.append(topic)

In [103]:
pd.DataFrame([topics[29]]+[topics[33]]+[topics[35]])

0          1               2         3               4  \
0  контроллер       звук          символ  блокчейн          корпус   
1        игра       файл      устройство    сервер            сайт   
2   галактика  вселенная  тёмный_энергия  инфляция  тёмный_материя   

              5                     6        7                   8  \
0     нейросеть           презентация  дисплей             наушник   
1        клиент                объект   сервис           программа   
2  млечный_путь  расширение_вселенная  материя  вещество_излучение   

                9  
0        текстура  
1         продукт  
2  энергия_вакуум

Изменились показатели перплексии, стали лучше (ниже). Coherence имеет более выраженные значения (что-то ниже, но пики выше). В целом, остались претензии по странным словам в топе. Они, как кажется, из кода в этих статьях. Не все темы легко интерпретировать из-за этого, поэтому выводы сделать трудно (кроме как по показателям)

### Разложение матриц в sklearn

Вернем униграммные тексты

In [104]:
from sklearn.decomposition import NMF
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer
import pandas as pd

Sklearn принимает на вход строки, поэтому склеим наши списки.

In [111]:
stexts = [' '.join(text) for text in texts]

Сделаем матрицу слова-документы с помощью TfidfVectorizer

In [113]:
vectorizer = TfidfVectorizer(max_features=25000, min_df=5, max_df=0.3, lowercase=False)
X = vectorizer.fit_transform(stexts)

Разложим её.

In [114]:
model = NMF(n_components=30)

In [115]:
model.fit(X)

NMF(alpha=0.0, beta_loss='frobenius', init=None, l1_ratio=0.0, max_iter=200,
  n_components=30, random_state=None, shuffle=False, solver='cd',
  tol=0.0001, verbose=0)

In [116]:
def get_nmf_topics(model, n_top_words):
    
    #id слов.
    feat_names = vectorizer.get_feature_names()
    
    word_dict = {};
    for i in range(30):
        
        #топ n слов для темы.
        words_ids = model.components_[i].argsort()[:-n_top_words - 1:-1]
        words = [feat_names[key] for key in words_ids]
        word_dict['Topic # ' + '{:02d}'.format(i+1)] = words;
    
    return pd.DataFrame(word_dict);

In [117]:
get_nmf_topics(model, 10)

Topic # 01 Topic # 02 Topic # 03   Topic # 04 Topic # 05  Topic # 06  \
0           продукт     public       игра  космический       сеть       рынок   
1         сотрудник       void      игрок      спутник     трафик    блокчейн   
2       программист        new    игровой       орбита      связь  российский   
3              язык     string     играть       ракета   оператор      страна   
4            клиент    private   персонаж         марс   интернет      бизнес   
5              опыт     return      steam      аппарат      канал      россия   
6  программирование      class         vr        земля      пакет      деньга   
7            бизнес     static      unity      станция    станция     миллион   
8              идея      класс     движок         наса    сетевой       рубль   
9              курс        var   геймплей         луна   протокол  финансовый   

  Topic # 07   Topic # 08 Topic # 09     Topic # 10      ...       Topic # 21  \
0         lt   устройство        the             ия      ...             сайт   
1         gt       камера         to       обучение      ...         страница   
2        div     смартфон         of      нейросеть      ...          реклама   
3     return      android        and      интеллект      ...           google   
4      const      телефон         in       машинный      ...          браузер   
5  компонент    мобильный         is  искусственный      ...          контент   
6      input        экран         on      нейронный      ...        рекламный   
7      react  аккумулятор        for    изображение      ...            домен   
8        int        apple        you       алгоритм      ...           клиент   
9       html       датчик       from           сеть      ...        аудитория   

  Topic # 22  Topic # 23  Topic # 24  Topic # 25  Topic # 26    Topic # 27  \
0         if      объект         бот        файл      сервер          тест   
1     return    значение   сообщение       папка      запрос  тестирование   
2       else     элемент    telegram      скрипт        база           end   
3        amp       метод         чат      строка      сервис      тестовый   
4        end       класс       канал       пакет       домен   тестировать   
5        var        блок         api      модуль          ip    библиотека   
6        int    алгоритм    телеграм  директория      клиент        ошибка   
7   function  переменный      сервис        sudo  сертификат   тестировщик   
8       true        язык  мессенджер      сборка        ключ            do   
9      false      строка         bot   настройка       адрес          test   

       Topic # 28  Topic # 29     Topic # 30  
0           центр        звук          робот  
1            дата      сигнал     автомобиль  
2  инфраструктура     наушник         машина  
3        облачный   усилитель        ребёнок  
4          услуга     частота         датчик  
5    оборудование    звуковой    беспилотный  
6          облако      музыка  робототехника  
7             цод   искажение       движение  
8          клиент  напряжение           lego  
9          сервис         ток       скорость  

[10 rows x 30 columns]

In [118]:
model.reconstruction_err_

59.56055287212584

In [120]:
min_df = [5, 10, 20]
max_df = [0.3, 0.5, 0.7]
ngram_range = [(1,1), (1,2), (1,3)]
max_features = [1000, 5000, 10000, 20000, 30000]

In [121]:
for i in product(min_df, max_df, ngram_range, max_features):
    vectorizer = TfidfVectorizer(max_features=i[3], min_df=i[0], max_df=i[1], ngram_range=i[2], lowercase=False)
    X = vectorizer.fit_transform(stexts)
    model = NMF(n_components=30)
    model.fit(X)
    print (i, model.reconstruction_err_)

(5, 0.3, (1, 1), 1000) 55.037983195903045
(5, 0.3, (1, 1), 5000) 58.74421224029299
(5, 0.3, (1, 1), 10000) 59.474488399583656
(5, 0.3, (1, 1), 20000) 59.55951689657057
(5, 0.3, (1, 1), 30000) 59.55351366439521
(5, 0.3, (1, 2), 1000) 54.96505093148022
(5, 0.3, (1, 2), 5000) 58.603516284453534
(5, 0.3, (1, 2), 10000) 59.45580792716226
(5, 0.3, (1, 2), 20000) 59.95199531880847
(5, 0.3, (1, 2), 30000) 60.17612783370688
(5, 0.3, (1, 3), 1000) 55.01303271465865
(5, 0.3, (1, 3), 5000) 58.60238587423807
(5, 0.3, (1, 3), 10000) 59.45098790479944
(5, 0.3, (1, 3), 20000) 59.94319856832916
(5, 0.3, (1, 3), 30000) 60.1838179502802
(5, 0.5, (1, 1), 1000) 54.1327013392443
(5, 0.5, (1, 1), 5000) 58.238111360714825
(5, 0.5, (1, 1), 10000) 59.08342216646864
(5, 0.5, (1, 1), 20000) 59.183977567286355
(5, 0.5, (1, 1), 30000) 59.16074516261151
(5, 0.5, (1, 2), 1000) 54.07341579690697
(5, 0.5, (1, 2), 5000) 58.15224510597516
(5, 0.5, (1, 2), 10000) 59.03152995171975
(5, 0.5, (1, 2), 20000) 59.60507372103507

Ошибка восстановления примерно та же, так что выберем какие-то средние значения

In [122]:
vectorizer = TfidfVectorizer(max_features=20000, min_df=10, max_df=0.5, lowercase=False)
X = vectorizer.fit_transform(stexts)
model = NMF(n_components=30)
model.fit(X)
get_nmf_topics(model, 10)

Topic # 01 Topic # 02   Topic # 03    Topic # 04   Topic # 05  Topic # 06  \
0    человек         lt         игра        учёный       камера    компания   
1        ваш         gt        игрок          мозг   устройство       рынок   
2        что        div      игровой       пациент     смартфон   сотрудник   
3      какой     return       играть        клетка      телефон      бизнес   
4       дело      const     персонаж       человек  аккумулятор  российский   
5     хотеть  компонент  разработчик  исследование        экран     миллион   
6     вопрос      input        steam   заболевание       датчик       рубль   
7      знать        int        unity       болезнь        видео     крупный   
8      жизнь        std           vr           ген       корпус         000   
9   проблема       html      уровень      организм         цена      россия   

     Topic # 07 Topic # 08        Topic # 09     Topic # 10     ...       \
0    приложение     public              язык          атака     ...        
1       android       void               код   безопасность     ...        
2     мобильный        new  программирование     уязвимость     ...        
3  пользователь     string       программист     устройство     ...        
4           ios    private               php  злоумышленник     ...        
5        google     return         программа         пароль     ...        
6    устройство      class              java           сеть     ...        
7           app     static           перевод         защита     ...        
8     платформа      класс            python         доступ     ...        
9           api        var        библиотека           ключ     ...        

     Topic # 21    Topic # 22 Topic # 23  Topic # 24    Topic # 25  \
0          сайт        печать         if     windows        проект   
1      страница       принтер       else   microsoft        задача   
2       реклама            3d     return       linux       команда   
3  пользователь        станок        end      версия       продукт   
4        клиент      материал        amp  обновление    разработка   
5         товар       пластик        int          10   разработчик   
6       контент  производство       true      studio          тест   
7       браузер            мм   function     браузер  тестирование   
8     рекламный        деталь        var      visual       решение   
9        скидка       изделие      false       azure      заказчик   

     Topic # 26        Topic # 27      Topic # 28  Topic # 29   Topic # 30  
0           бот             книга           центр      сигнал  виртуальный  
1     сообщение              часы            дата        звук       машина  
2      telegram  профессиональный          услуга     частота           вм  
3  пользователь   порекомендовать    оборудование   усилитель    резервный  
4           чат      предпочитать  инфраструктура     наушник        veeam  
5         канал           слушать        облачный   искажение  копирование  
6      телеграм              путь             цод    звуковой       vmware  
7    мессенджер            музыка          клиент       канал         диск  
8           api      пользоваться          облако  напряжение         хост  
9        сервис          бумажный       провайдер  устройство      vsphere  

[10 rows x 30 columns]

В целом то же самое. Хорошие темы 4,5, 10.
От LDA отличается тем, что более интерпретируемые слова, а там что-то специфическое в большинстве тем.